In [1]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import scanpy as sc
import scipy.io as sio
import anndata as ad
import seaborn as sns
import os as os
import sys as sys
sys.path.append('/home/qiuaodon/Desktop/PanCancer_scRNA_analysis/utils/')
from scRNA_utils import *
import operator as op
import matplotlib.colors as mcolors
data_dir_NHDP = "/home/qiuaodon/Desktop/project_data_new/"
data_dir = "/home/qiuaodon/Desktop/PanCancer_scRNA_analysis/CD4_CD8_final_version/"

## check the patients I can use with enough cells in subtypes


In [2]:
adata_T = sc.read(data_dir_NHDP + '1863-counts_cells_cohort1_T_cells_annotated.h5ad')

In [3]:
# get adata_CD4EX and adata_CD8EX
adata_CD4EX = adata_T[adata_T.obs['cell_type'] == 'CD4 EX', :]
adata_CD8EX = adata_T[adata_T.obs['cell_type'] == 'CD8 EX', :]

In [4]:
# check the number of cells for sample_id, find the patient_ids with more than 5 cells in both pre and on timepoints
cell_counts = adata_CD4EX.obs.groupby(['patient_id', 'timepoint'])['sample_id'].count().unstack()

# Filter patients with more than 5 cells in both 'pre' and 'on' timepoints
valid_patients_CD4EX = cell_counts[(cell_counts['pre'] > 5) & (cell_counts['on'] > 5)].index.tolist()
valid_patients_CD4EX = set(valid_patients_CD4EX)
# check the number of cells for sample_id, find the patient_ids with more than 5 cells in both pre and on timepoints in CD8EX
cell_counts = adata_CD8EX.obs.groupby(['patient_id', 'timepoint'])['sample_id'].count().unstack()

# Filter patients with more than 5 cells in both 'pre' and 'on' timepoints
valid_patients_CD8EX = cell_counts[(cell_counts['pre'] > 5) & (cell_counts['on'] > 5)].index.tolist()
valid_patients_CD8EX = set(valid_patients_CD8EX)

/tmp/ipykernel_3292344/2168074212.py:2: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  cell_counts = adata_CD4EX.obs.groupby(['patient_id', 'timepoint'])['sample_id'].count().unstack()
/tmp/ipykernel_3292344/2168074212.py:8: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  cell_counts = adata_CD8EX.obs.groupby(['patient_id', 'timepoint'])['sample_id'].count().unstack()


In [9]:
adata_M = sc.read(data_dir_NHDP + 'mye.h5ad')

In [ ]:
adata_Mono = adata_M[adata_M.obs['cell_type'] == 'Monocyte', :]

In [ ]:
# check the number of cells for sample_id, find the patient_ids with more than 5 cells in both pre and on timepoints
cell_counts = adata_Mono.obs.groupby(['patient_id', 'timepoint'])['sample_id'].count().unstack()

# Filter patients with more than 5 cells in both 'pre' and 'on' timepoints
valid_patients_Mono = cell_counts[(cell_counts['pre'] > 5) & (cell_counts['on'] > 5)].index.tolist()
valid_patients_Mono = set(valid_patients_Mono)

/tmp/ipykernel_3389877/292830472.py:2: FutureWarning: The default of observed=False is deprecated and will be changed to True in a future version of pandas. Pass observed=False to retain current behavior or observed=True to adopt the future default and silence this warning.
  cell_counts = adata_M1.obs.groupby(['patient_id', 'timepoint'])['sample_id'].count().unstack()


# get the DEGs of filtered patients of CD8EX and Mono

In [ ]:
Patients_CD8EX_Mono = list(valid_patients_CD8EX & valid_patients_Mono)
adata_CD8EX_1 = adata_CD8EX[adata_CD8EX.obs['patient_id'].isin(Patients_CD8EX_Mono), :]
adata_Mono_1 = adata_Mono[adata_Mono.obs['patient_id'].isin(Patients_CD8EX_Mono), :]

In [17]:
DEG_1 = paird_ttest(adata_CD8EX_1, condition_key = 'timepoint', sample_id_col = 'sample_id', patient_id_col = 'patient_id')
DEG_1 = DEG_1[DEG_1['pval'] < 0.01]

Input adata is not pseudo-bulk RNA data. Convert to pseudo-bulk RNA data.


/home/qiuaodon/Desktop/PanCancer_scRNA_analysis/utils/scRNA_utils.py:490: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  res_df['pval'] = res_df['pval'].replace([np.inf, -np.inf], np.nan)  # Replace infinite values with NaN


In [18]:
# remove the DEGs with . in the gene names
DEG_1 = DEG_1[~DEG_1.index.str.contains('\.')]

In [ ]:
DEG_2 = paird_ttest(adata_Mono_1, condition_key = 'timepoint', sample_id_col = 'sample_id', patient_id_col = 'patient_id')
DEG_2 = DEG_2[DEG_2['pval'] < 0.01]

Input adata is not pseudo-bulk RNA data. Convert to pseudo-bulk RNA data.


/home/qiuaodon/Desktop/PanCancer_scRNA_analysis/utils/scRNA_utils.py:490: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  res_df['pval'] = res_df['pval'].replace([np.inf, -np.inf], np.nan)  # Replace infinite values with NaN


In [21]:
DEG_2 = DEG_2[~DEG_2.index.str.contains('\.')]

## IVA

In [ ]:
adata_1_pseudo = scRNA2PseudoBulkAnnData(adata_CD8EX_1, sample_id_col='sample_id')
adata_2_pseudo = scRNA2PseudoBulkAnnData(adata_Mono_1, sample_id_col='sample_id')

In [ ]:
gene_1 = DEG_1.index.tolist()
gene_2 = DEG_2.index.tolist()

# Filter out invalid gene names
gene_1 = [gene for gene in gene_1 if gene in adata_1_pseudo.var_names]
gene_2 = [gene for gene in gene_2 if gene in adata_2_pseudo.var_names]

gene_1_matrix = adata_1_pseudo[:, gene_1].X
gene_2_matrix = adata_2_pseudo[:, gene_2].X
gene_1_df = pd.DataFrame(gene_1_matrix, columns=gene_1, index=adata_1_pseudo.obs['sample_id'])
gene_2_df = pd.DataFrame(gene_2_matrix, columns=gene_2, index=adata_2_pseudo.obs['sample_id'])
gene_1_df.columns = [i + '_T' for i in gene_1_df.columns]
gene_2_df.columns = [i + '_M' for i in gene_2_df.columns]
gene_df = gene_1_df
gene_df = pd.merge(gene_df, gene_2_df, on='sample_id')
gene_df['treatment'] = gene_df.index.str.contains('On').astype(int)
# get patient id from sample id remove the _On or _Pre
gene_df['patient_id'] = gene_df.index.str.replace('_On', '').str.replace('_Pre', '')

In [28]:
# export the gene_df to csv
gene_df.to_csv(data_dir + 'gene_df_CD8EX_Mono.csv')

## load in IV result and perform CIT

In [29]:
DEG_pairs = pd.read_excel(data_dir + 'IV_regression_results_with_FisherZ_CD8EX_Mono.xlsx')

In [30]:
DEG_pairs = DEG_pairs.rename(columns = {'gene_T':'g1', 'gene_cell':'g2'})
calculate_gene_correlation(DEG_pairs, adata_1_pseudo, adata_2_pseudo)

/home/qiuaodon/Desktop/PanCancer_scRNA_analysis/utils/scRNA_utils.py:914: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '-0.6109955956474308' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  results.loc[index, 'g1vsg2_correlation'] = corr_g1_g2


g1         g2  p_value_iv  r_squared_iv  p_value_ci  q_value_iv  \
0     ANKS1B_T    ABCD1_M    0.122261      0.326197    0.869144    0.163763   
1     ANKS1B_T    APOL4_M    0.005194      0.565479    0.562721    0.124380   
2     ANKS1B_T   ARMCX1_M    0.081800     -0.767757    0.006347    0.142035   
3     ANKS1B_T  ATP5F1E_M    0.169402     -0.511336    0.051200    0.195944   
4     ANKS1B_T  ATP5MC3_M    0.093907      0.078211    0.403346    0.148456   
...        ...        ...         ...           ...         ...         ...   
4395  ZNF600_T   ZNF146_M    0.004446      0.569319    0.531256    0.124380   
4396  ZNF600_T   ZNF185_M    0.163235     -0.447008    0.066718    0.191951   
4397  ZNF600_T   ZNF430_M    0.007964      0.137792    0.031665    0.124380   
4398  ZNF600_T   ZNF623_M    0.022447      0.209888    0.220712    0.124380   
4399  ZNF600_T    KCNE1_M    0.053493     -0.480399    0.017058    0.129100   

      q_value_ci  g1vsg2_correlation  
0       0.884830           -0.610996  
1       0.602867            0.781715  
2       0.046414           -0.208822  
3       0.112024            0.096239  
4       0.455291            0.457321  
...          ...                 ...  
4395    0.573492            0.785351  
4396    0.129612           -0.129037  
4397    0.088582            0.677865  
4398    0.281406            0.612019  
4399    0.066409           -0.353366  

[4400 rows x 8 columns]

In [31]:
# Combine the two conditions using the logical OR operator
DEG_pairs = DEG_pairs[(DEG_pairs['g1vsg2_correlation'] > 0.6) | (DEG_pairs['g1vsg2_correlation'] < -0.6)]
DEG_pairs = DEG_pairs[(DEG_pairs['p_value_ci'] > 0.1)]
# sort the DEG_pairs by g1vsg2_correlation
DEG_pairs = DEG_pairs.sort_values(by='g1vsg2_correlation', ascending=False)
DEG_pairs

g1        g2  p_value_iv  r_squared_iv  p_value_ci  q_value_iv  \
1658     DUSP1_T   THYN1_M    0.000088      0.815784    0.245213    0.124380   
815       CD55_T    GFM2_M    0.000217      0.749369    0.714198    0.124380   
1092      CISH_T     MNT_M    0.002353      0.715428    0.881760    0.124380   
3285  RASGEF1B_T  KBTBD7_M    0.000693      0.701303    0.611094    0.124380   
4384    ZNF600_T    TCF4_M    0.003640      0.688899    0.850472    0.124380   
...          ...       ...         ...           ...         ...         ...   
2554      IRF4_T  ARMCX1_M    0.000825      0.654188    0.801443    0.124380   
4119     ZFP36_T    TAF7_M    0.001625      0.643035    0.459401    0.124380   
2989    NFKBIA_T  ZNF430_M    0.000203      0.667206    0.431841    0.124380   
1957     HMOX1_T    GALC_M    0.001602      0.705619    0.667241    0.124380   
1672     DUSP4_T   ABCD1_M    0.031154      0.682245    0.443179    0.124821   

      q_value_ci  g1vsg2_correlation  
1658    0.306076            0.916963  
815     0.742024            0.876258  
1092    0.895601            0.857419  
3285    0.646972            0.853715  
4384    0.868232            0.843172  
...          ...                 ...  
2554    0.823529           -0.823717  
4119    0.507116           -0.829982  
2989    0.482503           -0.835186  
1957    0.697930           -0.856171  
1672    0.493294           -0.858346  

[534 rows x 8 columns]

In [32]:
lrpair = pd.read_csv('/home/qiuaodon/Desktop/project_data_new/lr_network_unique.tsv', sep='\t')

In [33]:
# remove the ppi_prediction and ppi_prediction_go
lrpair = lrpair[lrpair['database'] != 'ppi_prediction']
lrpair = lrpair[lrpair['database'] != 'ppi_prediction_go']
lrpair = lrpair[['from', 'to']]
# change from as L and to as R
lrpair.columns = ['L', 'R']
lrpair

L      R
0      CXCL1  CXCR2
1      CXCL2  CXCR2
2      CXCL3  CXCR2
3      CXCL5  CXCR2
4       PPBP  CXCR2
...      ...    ...
1387  COL2A1   SDC1
1388   LAMA1   SV2A
1389  COL2A1    GP6
1390   LAMA1   DAG1
1391  CCL3L3   CCR1

[1392 rows x 2 columns]

In [34]:
# Check expression in adata_1_pseudo
expressed_genes_1 = adata_1_pseudo.var_names[adata_1_pseudo.X.sum(axis=0) > 0].tolist()

# Check expression in adata_2_pseudo
expressed_genes_2 = adata_2_pseudo.var_names[adata_2_pseudo.X.sum(axis=0) > 0].tolist()

# Filter lrpair where both L and R are expressed in their respective datasets
lrpair = lrpair[
    (lrpair['L'].isin(expressed_genes_1)) & 
    (lrpair['R'].isin(expressed_genes_2))
].reset_index(drop=True)
lrpair

L      R
0     CXCL1  CXCR2
1     CXCL2  CXCR2
2     CXCL8  CXCR2
3     CXCL9  CXCR3
4    CXCL10  CXCR3
..      ...    ...
427  COL2A1  ITGAV
428  COL2A1  ITGB8
429  COL2A1   CD44
430  COL2A1   SDC1
431  COL2A1    GP6

[432 rows x 2 columns]

## CIT Fisherz

In [35]:
results = CIT_test(DEG_pairs, lrpair, adata_1_pseudo, adata_2_pseudo, gene_df, method = 'fisherz', p_value_threshold=0.05)

/home/qiuaodon/anaconda3/lib/python3.11/site-packages/numpy/lib/function_base.py:2897: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
/home/qiuaodon/anaconda3/lib/python3.11/site-packages/numpy/lib/function_base.py:2898: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]
/home/qiuaodon/anaconda3/lib/python3.11/site-packages/numpy/lib/function_base.py:2897: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
/home/qiuaodon/anaconda3/lib/python3.11/site-packages/numpy/lib/function_base.py:2898: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]
/home/qiuaodon/anaconda3/lib/python3.11/site-packages/numpy/lib/function_base.py:2897: RuntimeWarning: invalid value encountered in divide
  c /= stddev[:, None]
/home/qiuaodon/anaconda3/lib/python3.11/site-packages/numpy/lib/function_base.py:2898: RuntimeWarning: invalid value encountered in divide
  c /= stddev[None, :]
/home/qiuaodon/anaconda3/lib

In [36]:
#calculate the correlation between g1 and g2
calculate_gene_correlation(results, adata_1_pseudo, adata_2_pseudo)
calculate_residuals_correlation(results, adata_1_pseudo, adata_2_pseudo)

/home/qiuaodon/Desktop/PanCancer_scRNA_analysis/utils/scRNA_utils.py:914: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '0.8270804121768967' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  results.loc[index, 'g1vsg2_correlation'] = corr_g1_g2
/home/qiuaodon/Desktop/PanCancer_scRNA_analysis/utils/scRNA_utils.py:1060: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '0.5112363065826633' has dtype incompatible with int64, please explicitly cast to a compatible dtype first.
  results.at[index, 'g1_residualvsg2_residuals_correlation'] = corr


g1         g2        L         R    pValue  g1vsg2_correlation  \
0      CD160_T     MADD_M  TNFSF14  TNFRSF14  0.050566            0.827080   
1        TNF_T   RNF216_M      TNF  TNFRSF1B  0.085510            0.804610   
2        TNF_T   RNF216_M      TNF  TNFRSF1A  0.131689            0.804610   
3        TNF_T   RNF216_M      TNF      LTBR  0.102866            0.804610   
4     CEMIP2_T    NLRP3_M    VCAM1     ITGB2  0.128303            0.784677   
...        ...        ...      ...       ...       ...                 ...   
3095   DUSP4_T     GALC_M      TNF  TNFRSF1A  0.055307           -0.777979   
3096   HMOX1_T   RNF216_M      TNF  TNFRSF1A  0.118047           -0.784144   
3097   HMOX1_T   RNF216_M      TNF      LTBR  0.064155           -0.784144   
3098   HMOX1_T  SPTY2D1_M     GZMB     IGF2R  0.056563           -0.791894   
3099   HMOX1_T   DNAJC5_M      TNF  TNFRSF1A  0.054432           -0.809790   

      g1_residualvsg2_residuals_correlation  
0                                  0.511236  
1                                  0.459280  
2                                  0.409633  
3                                  0.438896  
4                                  0.412836  
...                                     ...  
3095                              -0.502939  
3096                              -0.422890  
3097                              -0.488712  
3098                              -0.500827  
3099                              -0.504431  

[3100 rows x 7 columns]

In [37]:
results_filtered = results[(results['pValue'] > 0.1)]
results_filtered = results_filtered[(results_filtered['g1_residualvsg2_residuals_correlation'] < 0.3)]
results_filtered = results_filtered[(results_filtered['g1_residualvsg2_residuals_correlation'] > -0.3)]
results_filtered 

g1        g2      L         R    pValue  g1vsg2_correlation  \
8         TNF_T  DNAJC5_M    TNF  TNFRSF1B  0.381878            0.768223   
9         TNF_T  DNAJC5_M    TNF  TNFRSF1A  0.389852            0.768223   
18      RAB38_T   APOL4_M    MPZ       MPZ  0.318548            0.753692   
107     RAB38_T    MYOF_M   SPP1     ITGA4  0.318162            0.715720   
109     RAB38_T    MYOF_M   SPP1     ITGAV  0.431380            0.715720   
...         ...       ...    ...       ...       ...                 ...   
3035      TNF_T  SLC1A3_M    TNF  TNFRSF1A  0.775362           -0.698479   
3036      TNF_T  SLC1A3_M    TNF      LTBR  0.452553           -0.698479   
3039     CAPG_T   CD163_M  VCAM1     ITGB1  0.292278           -0.701586   
3044    HMOX1_T  ZNF146_M    TNF  TNFRSF1A  0.318624           -0.707357   
3059  BCL2L11_T    LBX2_M    TNF  TNFRSF1B  0.616787           -0.712519   

      g1_residualvsg2_residuals_correlation  
8                                  0.247201  
9                                  0.243252  
18                                 0.280236  
107                                0.280447  
109                                0.223312  
...                                     ...  
3035                              -0.082193  
3036                              -0.213507  
3039                              -0.294982  
3044                              -0.280194  
3059                              -0.143459  

[143 rows x 7 columns]

In [38]:
results_filtered['L_R'] = results_filtered['L'] + '_' + results_filtered['R']
results_filtered['L_R'].nunique()

24

In [40]:
results.to_csv(data_dir + 'CIT_test_results_CD8EX_Mono_results.csv')

In [56]:
import pandas as pd
import numpy as np

# Sample data (assuming results_filtered is already available)
# Adjusting the script to use absolute mean and determine final sign based on majority sign

grouped_results = results_filtered.groupby(["L", "R"])

# Create a new DataFrame to hold the GEM1 and GEM2 groupings
tracked_gem1 = set()
tracked_gem2 = set()

min_gene_num = 2

# Temporary list to hold data before creating DataFrame
temp_data = []

for (ligand, receptor), group in grouped_results:
    gem1 = group["g1"].drop_duplicates().tolist()
    gem2 = group["g2"].drop_duplicates().tolist()
    
    # Calculate mean correlation values using absolute mean
    g1vsg2_corr_mean = np.abs(group["g1vsg2_correlation"]).mean()
    g1_res_vs_g2_res_mean = np.abs(group["g1_residualvsg2_residuals_correlation"]).mean()
    p_value_mean = group["pValue"].mean()
    
    # Determine final sign based on majority sign of correlations
    sign_g1vsg2 = np.sign(group["g1vsg2_correlation"]).sum()
    sign_g1_res_vs_g2_res = np.sign(group["g1_residualvsg2_residuals_correlation"]).sum()
    
    final_g1vsg2_corr = g1vsg2_corr_mean * (1 if sign_g1vsg2 >= 0 else -1)
    final_g1_res_vs_g2_res = g1_res_vs_g2_res_mean * (1 if sign_g1_res_vs_g2_res >= 0 else -1)
    
    # Check the overlap between current GEM_g1 and previously tracked GEM_g1
    overlap_gem1 = len(set(gem1) & tracked_gem1)
    overlap_gem2 = len(set(gem2) & tracked_gem2)
    
    # Filter to include only those with at least three genes in GEM_g1
    if len(gem1) > min_gene_num:
        temp_data.append({
            "Ligand": ligand,
            "Receptor": receptor,
            "GEM1_elements": gem1,
            "GEM2_elements": gem2,
            "Num_genes_GEM1": len(gem1),
            "Num_genes_GEM2": len(gem2),
            "GEM1vsGEM2_corr(mean)": final_g1vsg2_corr,
            "GEM1_residualvsGEM2_residual_corr(mean)": final_g1_res_vs_g2_res,
            "average_significance": p_value_mean
        })
        # Update the tracked GEM_g1 and GEM_g2 sets
        tracked_gem1.update(gem1)
        tracked_gem2.update(gem2)

# Convert the temporary data to a DataFrame
grouped_df = pd.DataFrame(temp_data)
grouped_df

Ligand   Receptor                                      GEM1_elements  \
0       CFH       SELL               [RAB38_T, CARMIL3_T, MPZ_T, PELI1_T]   
1       LTB       LTBR                      [TSC22D3_T, DNAJB1_T, ERN1_T]   
2      SPP1      ITGA4                        [RAB38_T, CARMIL3_T, MPZ_T]   
3      SPP1      ITGAV                        [RAB38_T, CARMIL3_T, MPZ_T]   
4       TNF       LTBR  [RASGEF1B_T, TNF_T, IER2_T, TSC22D3_T, NFKBIA_...   
5       TNF   TNFRSF1A  [TNF_T, IER2_T, NFKBIA_T, ZNF600_T, HMOX1_T, C...   
6       TNF   TNFRSF1B  [TNF_T, ATF3_T, IER2_T, PELI1_T, BCL2L11_T, PR...   
7   TNFSF10  TNFRSF10B                 [IER2_T, ZNF600_T, DUSP4_T, TNF_T]   
8   TNFSF14       LTBR                      [CD160_T, ZFP36_T, TSC22D3_T]   
9     VCAM1      ITGB1                        [CEMIP2_T, IL6ST_T, CAPG_T]   
10    VCAM1      ITGB2               [CEMIP2_T, IL6ST_T, CD160_T, CAPG_T]   

                                        GEM2_elements  Num_genes_GEM1  \
0                                            [MYOF_M]               4   
1   [RHOB_M, CRKL_M, ZNF623_M, USF1_M, RNF216_M, A...               3   
2                                            [MYOF_M]               3   
3                                            [MYOF_M]               3   
4   [RNF216_M, CRKL_M, SPTY2D1_M, USF1_M, CDC25B_M...               9   
5   [DNAJC5_M, LBX2_M, KLF13_M, GALC_M, DUSP6_M, R...              10   
6   [DNAJC5_M, LBX2_M, MYOF_M, GALC_M, DUSP6_M, RN...               9   
7                                  [KBTBD7_M, SEM1_M]               4   
8          [RAB11FIP1_M, ATP5F1E_M, USF1_M, NHLRC2_M]               3   
9                          [CD163_M, NLRP3_M, MADD_M]               3   
10                [CD163_M, NLRP3_M, CUL4A_M, MADD_M]               4   

    Num_genes_GEM2  GEM1vsGEM2_corr(mean)  \
0                1               0.675225   
1                7              -0.623354   
2                1               0.692487   
3                1               0.692487   
4               16               0.631740   
5               14              -0.641231   
6               12               0.642562   
7                2              -0.609772   
8                4               0.624286   
9                3              -0.668510   
10               4               0.642358   

    GEM1_residualvsGEM2_residual_corr(mean)  average_significance  
0                                  0.226690              0.429772  
1                                 -0.226296              0.434479  
2                                  0.233989              0.411808  
3                                  0.178621              0.534240  
4                                 -0.179060              0.544880  
5                                 -0.182521              0.535026  
6                                  0.174191              0.554074  
7                                 -0.204088              0.476836  
8                                  0.224913              0.444520  
9                                 -0.246193              0.392787  
10                                 0.246922              0.383133

In [58]:
# rank each GEM_g1 by order of name inside
grouped_df['GEM1_elements'] = grouped_df['GEM1_elements'].apply(lambda x: sorted(x))
grouped_df['GEM1_elements'] = grouped_df['GEM1_elements'].apply(lambda x: sorted(x))

In [59]:
# save the grouped_df to excel
grouped_df.to_excel(data_dir + 'CIT_results_CD8EXvsMono_groupedLR.xlsx')

In [ ]:
# Load the grouped dataframe from the Excel file
grouped_df = pd.read_excel(data_dir + 'CIT_results_CD8EXvsMono_groupedLR.xlsx')

# Display the first few rows to confirm it loaded correctly
grouped_df.head()